# Create a dataset
This jupyter notebook is dedicated to creating a dataset for the picture cross puzzle. Here we got two ways of creating the puzzle. One is randomly generated order is to see the picture as a binary number. We are going to explain them later in this notebook.

In [1]:
import numpy as np
from random import randint

Here we set the shape of the picture we want. We start the picture cross solver in the easy mode. So we are going for something simple and not too big. Also, the 4x4 matrix allows a total of 65536 (2^16) configuration, which is enough data to create a neural network to solve it. The 3x3 matrix only has 512 (2^9) that could not be enough for training.

In [2]:
shape = (4,4)
shape

(4, 4)

This is the first method to create an image using random. For every position in the matrix, we use randint to set 0 or 1 in that position. The problem with this method is that we could end up with a duplicated picture.

In [3]:
def create_board(shape):
    board = np.full(shape, 0)

    for i in range(shape[0]):
        for j in range(shape[1]):
            x = randint(0,1)
            if x:
                board[i][j] = 1
    #         print(i, j, x)
#     print(board)
    return board

The following blocks of code if for creating the x from the dataset. This block of code will return the tip to fill the lines of the picture. 

It goes to every position of the picture. If there is a 1 then it starting counting, it only stops when it reaches a 0 or the end of the line. If it was a zero, it adds the counting to an array and then resets the counter. 

When we finish one line we add other zeros so that we have the same format to all lines. Notice that the max number of tips needed to solve the line is the ceiling of the half of the line size. If we had one line with 1s followed by 0s all the way than the max number of tips would be reached. for example, the line is \[10101\], with a size of 5 and the tips would be \[111\], with size of 3 which is ceil(5/2)=ceil(2.5)=3.

In [4]:
#line
def count_lines(board, shape):
    count_lines = []
    for i in range(shape[0]):
#         print(board[i])
        count = 0
        count_line = []
        for j in range(shape[1]):
            if board[i][j]:
                count += 1
            if (board[:,j][i] == 0 or j == shape[1]-1) and count != 0:
                count_line.append(count)
                count = 0
        [count_line.append(0) for k in range(int(np.ceil(shape[1]/2)) - len(count_line))]
#         print(count_line)
        count_lines.append(count_line)
#     print(count_lines)
    return count_lines

The exact same thing is done but for the column. We had to use the indexation from numpy to reach each position of the column instead of the lines on this code.

In [5]:
#row
def count_rows(board, shape):
    count_rows = []
    for j in range(shape[1]):
    #     print(board[:,j])
        count = 0
        count_row = []
        for i in range(shape[0]):
    #         print(board[:,j][i])
            if board[:,j][i]:
                count += 1
            if (board[:,j][i] == 0 or i == shape[0]-1) and count != 0:
                count_row.append(count)
                count = 0
        [count_row.append(0) for k in range(int(np.ceil(shape[0]/2)) - len(count_row))]
    #     print(count_row)
        count_rows.append(count_row)
#     print(count_rows)
    return count_rows

Here is one example to the randomly generated "picture".

In [6]:
board = create_board(shape)
board

array([[1, 1, 0, 1],
       [0, 1, 1, 1],
       [0, 1, 1, 0],
       [1, 0, 1, 0]])

This is the tips for the line. We reshaped them so it would be just an array in the dataset. This was done to be easier to use as input in the neural network.

Each pair of numbers represents the tips for each line from the picture above. \[21\] stands for the first line \[1101\], \[30\] for \[0111\], and so on.

In [7]:
np.reshape(count_lines(board,shape), (-1))

array([2, 1, 3, 0, 2, 0, 1, 1])

This is the tips for the columns. It follows the same logic for the line mentioned above. \[11\] stands for the first column\[1001\], \[30\] for \[1110\], and etc.

In [8]:
np.reshape(count_rows(board,shape), (-1))

array([1, 1, 3, 0, 3, 0, 2, 0])

In [9]:
import math

This is the second method to create an image. Since we are only using a small image, we can see each matrix as a binary number. For example, the 2x2 matrix $\left[ \begin{array}{cc}
0 & 0 \\
0 & 0 \\ \end{array} \right]$ reshaped would be \[0000\] which is 0 in binary. $\left[ \begin{array}{cc}
0 & 0 \\
0 & 1 \\ \end{array} \right]$ would be \[0001\] which is 1 in binary, and etc.

So in this code, we go for every number that could be represented and reshaped it to a matrix. In the same time, we calculated the tips for the lines and columns and appended them to the variables data_x and data_y respectively.

In [10]:
shape = (4,4)

max_num = int(math.pow(2,(shape[0]*shape[1])))

data_x = []
data_y = []

for i in range(max_num):
    array = np.array([int(j) for j in format(i,"0"+str(shape[0]*shape[1])+"b")])
    board = array.reshape(shape)
#     print(i, board)
    data_x.append(np.append(np.reshape(count_lines(board,shape), (-1)), np.reshape(count_rows(board,shape), (-1))))
    data_y.append(board)
data_y = np.array(data_y)

We save the variables in the dataset folder.

In [12]:
np.save("dataset/data_y_4x4", data_y)
np.save("dataset/data_x_4x4", data_x)

We could load them.

In [3]:
data_x = np.load("dataset/data_x_4x4.npy")
data_y = np.load("dataset/data_y_4x4.npy")

To solve the puzzle we have to understand the problem. We are not expecting to solve 100% of the cases, but we can calculate how many of these cases are solvable. Having a number of problems that we can solve helps to know if we reached the best solution or if we are getting closer to it.

The first two lines of this code are the shape of data_x and data_y. both of them have 65536 cases. In the data_y the picture is in the shape of 4x4 array, while the data_x we concatenated the tips from line together with the tips from the column, resulting in an array of 16 for each case.

In the data_y each picture is unique as printed in the third line. But only 58196 are unique for the data_x. This means that the tip to solve one picture might be the same to solve another picture. It also means that 7340 cases have the same x as others. So we are expecting the neural network to fail in these cases. 

One example might be  $\left[ \begin{array}{cc}
1 & 0 \\
0 & 1 \\ \end{array} \right]$ and $\left[ \begin{array}{cc}
0 & 1 \\
1 & 0 \\ \end{array} \right]$ both have the same tips for line and column \[11\] and \[11\].

In [3]:
print(data_y.shape)
print(data_x.shape)
print(len(np.unique(data_y, axis=0)))
unique_x = np.unique(data_x, axis=0)
print(len(unique_x))
print(len(np.unique(data_y, axis=0))-len(unique_x))

(65536, 4, 4)
(65536, 16)
65536
58196
7340


But the 7340 cases calculated before is not the total number of cases the neural network is going to fail. This number is only those duplicated. We need the total of cases with the same x. np.unique only return the unique ones excluding the copies, but it doesn't say which case has copies. We need to find that. That is why we coded this.

For every unique x, we compare with every x from data_x. In the end, if we add those that have only one copy to the variable called unique.

In [24]:
unique = []
for i in unique_x:
    print(i)
    count = 0
    for j in data_x:
        if np.array_equal(i,j):
            count += 1
    if count==1:
        unique.append(i)
#     break
print(unique)

[0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]
[0 0 0 0 0 0 1 0 0 0 0 0 0 0 1 0]
[0 0 0 0 0 0 1 0 0 0 0 0 1 0 0 0]
[0 0 0 0 0 0 1 0 0 0 1 0 0 0 0 0]
[0 0 0 0 0 0 1 0 1 0 0 0 0 0 0 0]
[0 0 0 0 0 0 1 1 0 0 1 0 0 0 1 0]
[0 0 0 0 0 0 1 1 1 0 0 0 0 0 1 0]
[0 0 0 0 0 0 1 1 1 0 0 0 1 0 0 0]
[0 0 0 0 0 0 1 2 1 0 0 0 1 0 1 0]
[0 0 0 0 0 0 2 0 0 0 0 0 1 0 1 0]
[0 0 0 0 0 0 2 0 0 0 1 0 1 0 0 0]
[0 0 0 0 0 0 2 0 1 0 1 0 0 0 0 0]
[0 0 0 0 0 0 2 1 1 0 1 0 0 0 1 0]
[0 0 0 0 0 0 3 0 0 0 1 0 1 0 1 0]
[0 0 0 0 0 0 3 0 1 0 1 0 1 0 0 0]
[0 0 0 0 0 0 4 0 1 0 1 0 1 0 1 0]
[0 0 0 0 1 0 0 0 0 0 0 0 0 0 1 0]
[0 0 0 0 1 0 0 0 0 0 0 0 1 0 0 0]
[0 0 0 0 1 0 0 0 0 0 1 0 0 0 0 0]
[0 0 0 0 1 0 0 0 1 0 0 0 0 0 0 0]
[0 0 0 0 1 0 1 0 0 0 0 0 0 0 2 0]
[0 0 0 0 1 0 1 0 0 0 0 0 1 0 1 0]
[0 0 0 0 1 0 1 0 0 0 0 0 2 0 0 0]
[0 0 0 0 1 0 1 0 0 0 1 0 0 0 1 0]
[0 0 0 0 1 0 1 0 0 0 1 0 1 0 0 0]
[0 0 0 0 1 0 1 0 0 0 2 0 0 0 0 0]
[0 0 0 0 1 0 1 0 1 0 0 0 0 0 1 0]
[0 0 0 0 1 0 1 0 1 0 0 0 1 0 0 0]
[0 0 0 0 1 0 1 0 1 0 1 0 0 0 0 0]
[0 0 0 0 1 0 1

[0 0 1 0 0 0 1 0 0 0 1 0 1 0 0 0]
[0 0 1 0 0 0 1 0 0 0 1 1 0 0 0 0]
[0 0 1 0 0 0 1 0 1 0 0 0 0 0 1 0]
[0 0 1 0 0 0 1 0 1 0 0 0 1 0 0 0]
[0 0 1 0 0 0 1 0 1 0 1 0 0 0 0 0]
[0 0 1 0 0 0 1 0 1 1 0 0 0 0 0 0]
[0 0 1 0 0 0 1 1 0 0 1 0 0 0 1 1]
[0 0 1 0 0 0 1 1 0 0 1 0 1 0 1 0]
[0 0 1 0 0 0 1 1 0 0 1 1 0 0 1 0]
[0 0 1 0 0 0 1 1 1 0 0 0 0 0 1 1]
[0 0 1 0 0 0 1 1 1 0 0 0 1 0 1 0]
[0 0 1 0 0 0 1 1 1 0 0 0 1 1 0 0]
[0 0 1 0 0 0 1 1 1 0 1 0 0 0 1 0]
[0 0 1 0 0 0 1 1 1 0 1 0 1 0 0 0]
[0 0 1 0 0 0 1 1 1 1 0 0 0 0 1 0]
[0 0 1 0 0 0 1 1 1 1 0 0 1 0 0 0]
[0 0 1 0 0 0 1 2 1 0 0 0 1 0 1 1]
[0 0 1 0 0 0 1 2 1 0 0 0 1 1 1 0]
[0 0 1 0 0 0 1 2 1 0 1 0 1 0 1 0]
[0 0 1 0 0 0 1 2 1 1 0 0 1 0 1 0]
[0 0 1 0 0 0 2 0 0 0 0 0 1 0 1 1]
[0 0 1 0 0 0 2 0 0 0 0 0 1 1 1 0]
[0 0 1 0 0 0 2 0 0 0 1 0 1 0 1 0]
[0 0 1 0 0 0 2 0 0 0 1 0 1 1 0 0]
[0 0 1 0 0 0 2 0 0 0 1 1 1 0 0 0]
[0 0 1 0 0 0 2 0 1 0 0 0 1 0 1 0]
[0 0 1 0 0 0 2 0 1 0 1 0 0 0 1 0]
[0 0 1 0 0 0 2 0 1 0 1 0 1 0 0 0]
[0 0 1 0 0 0 2 0 1 0 1 1 0 0 0 0]
[0 0 1 0 0 0 2

[0 0 1 0 1 1 1 0 0 0 1 0 0 0 3 0]
[0 0 1 0 1 1 1 0 0 0 1 0 1 0 2 0]
[0 0 1 0 1 1 1 0 0 0 1 0 1 1 1 0]
[0 0 1 0 1 1 1 0 0 0 2 0 0 0 2 0]
[0 0 1 0 1 1 1 0 0 0 2 0 1 0 1 0]
[0 0 1 0 1 1 1 0 0 0 3 0 0 0 1 0]
[0 0 1 0 1 1 1 0 1 0 0 0 0 0 3 0]
[0 0 1 0 1 1 1 0 1 0 0 0 1 0 1 1]
[0 0 1 0 1 1 1 0 1 0 0 0 1 0 2 0]
[0 0 1 0 1 1 1 0 1 0 0 0 1 1 1 0]
[0 0 1 0 1 1 1 0 1 0 0 0 2 0 1 0]
[0 0 1 0 1 1 1 0 1 0 0 0 3 0 0 0]
[0 0 1 0 1 1 1 0 1 0 1 0 0 0 2 0]
[0 0 1 0 1 1 1 0 1 0 1 0 1 0 1 0]
[0 0 1 0 1 1 1 0 1 0 1 0 2 0 0 0]
[0 0 1 0 1 1 1 0 1 0 1 1 0 0 1 0]
[0 0 1 0 1 1 1 0 1 0 1 1 1 0 0 0]
[0 0 1 0 1 1 1 0 1 0 2 0 0 0 1 0]
[0 0 1 0 1 1 1 0 1 1 1 0 0 0 1 0]
[0 0 1 0 1 1 1 0 2 0 0 0 0 0 2 0]
[0 0 1 0 1 1 1 0 2 0 0 0 1 0 1 0]
[0 0 1 0 1 1 1 0 2 0 0 0 2 0 0 0]
[0 0 1 0 1 1 1 0 2 0 1 0 0 0 1 0]
[0 0 1 0 1 1 1 0 2 0 1 0 1 0 0 0]
[0 0 1 0 1 1 1 0 3 0 0 0 0 0 1 0]
[0 0 1 0 1 1 1 0 3 0 0 0 1 0 0 0]
[0 0 1 0 1 1 1 1 0 0 2 0 0 0 3 0]
[0 0 1 0 1 1 1 1 0 0 2 0 1 0 2 0]
[0 0 1 0 1 1 1 1 0 0 3 0 0 0 2 0]
[0 0 1 0 1 1 1

[0 0 1 0 2 0 1 1 1 0 2 0 2 0 0 0]
[0 0 1 0 2 0 1 1 1 0 3 0 0 0 1 0]
[0 0 1 0 2 0 1 1 1 1 0 0 1 0 2 0]
[0 0 1 0 2 0 1 1 1 1 0 0 2 0 1 0]
[0 0 1 0 2 0 1 1 1 1 1 0 1 0 1 0]
[0 0 1 0 2 0 1 1 1 1 1 0 2 0 0 0]
[0 0 1 0 2 0 1 1 2 0 1 0 0 0 1 1]
[0 0 1 0 2 0 1 1 2 0 1 0 1 0 1 0]
[0 0 1 0 2 0 1 1 2 0 1 0 1 1 0 0]
[0 0 1 0 2 0 1 1 2 0 2 0 0 0 1 0]
[0 0 1 0 2 0 1 1 2 0 2 0 1 0 0 0]
[0 0 1 0 2 0 1 1 3 0 1 0 0 0 1 0]
[0 0 1 0 2 0 1 1 3 0 1 0 1 0 0 0]
[0 0 1 0 2 0 1 2 1 0 0 0 2 0 3 0]
[0 0 1 0 2 0 1 2 1 0 0 0 3 0 2 0]
[0 0 1 0 2 0 1 2 1 0 1 0 2 0 1 1]
[0 0 1 0 2 0 1 2 1 0 1 0 2 0 2 0]
[0 0 1 0 2 0 1 2 1 0 1 0 3 0 1 0]
[0 0 1 0 2 0 1 2 1 0 2 0 2 0 1 0]
[0 0 1 0 2 0 1 2 1 1 0 0 2 0 2 0]
[0 0 1 0 2 0 1 2 1 1 1 0 2 0 1 0]
[0 0 1 0 2 0 1 2 2 0 1 0 1 0 1 1]
[0 0 1 0 2 0 1 2 2 0 1 0 1 1 1 0]
[0 0 1 0 2 0 1 2 2 0 2 0 1 0 1 0]
[0 0 1 0 2 0 1 2 3 0 1 0 1 0 1 0]
[0 0 1 0 2 0 2 0 0 0 0 0 2 0 3 0]
[0 0 1 0 2 0 2 0 0 0 0 0 3 0 2 0]
[0 0 1 0 2 0 2 0 0 0 1 0 2 0 1 1]
[0 0 1 0 2 0 2 0 0 0 1 0 2 0 2 0]
[0 0 1 0 2 0 2

[0 0 1 0 3 0 4 0 1 0 2 0 3 0 2 0]
[0 0 1 0 3 0 4 0 1 0 3 0 2 0 2 0]
[0 0 1 0 3 0 4 0 1 1 2 0 2 0 2 0]
[0 0 1 0 3 0 4 0 2 0 2 0 2 0 1 1]
[0 0 1 0 3 0 4 0 2 0 2 0 3 0 1 0]
[0 0 1 0 3 0 4 0 2 0 3 0 2 0 1 0]
[0 0 1 0 3 0 4 0 3 0 2 0 2 0 1 0]
[0 0 1 0 4 0 0 0 1 0 1 0 1 0 2 0]
[0 0 1 0 4 0 0 0 1 0 1 0 2 0 1 0]
[0 0 1 0 4 0 0 0 1 0 2 0 1 0 1 0]
[0 0 1 0 4 0 0 0 2 0 1 0 1 0 1 0]
[0 0 1 0 4 0 1 0 1 0 1 0 1 0 3 0]
[0 0 1 0 4 0 1 0 1 0 1 0 2 0 2 0]
[0 0 1 0 4 0 1 0 1 0 1 0 3 0 1 0]
[0 0 1 0 4 0 1 0 1 0 2 0 1 0 2 0]
[0 0 1 0 4 0 1 0 1 0 2 0 2 0 1 0]
[0 0 1 0 4 0 1 0 1 0 3 0 1 0 1 0]
[0 0 1 0 4 0 1 0 2 0 1 0 1 0 2 0]
[0 0 1 0 4 0 1 0 2 0 1 0 2 0 1 0]
[0 0 1 0 4 0 1 0 2 0 2 0 1 0 1 0]
[0 0 1 0 4 0 1 0 3 0 1 0 1 0 1 0]
[0 0 1 0 4 0 1 1 1 0 2 0 1 0 3 0]
[0 0 1 0 4 0 1 1 1 0 2 0 2 0 2 0]
[0 0 1 0 4 0 1 1 1 0 3 0 1 0 2 0]
[0 0 1 0 4 0 1 1 2 0 1 0 1 0 3 0]
[0 0 1 0 4 0 1 1 2 0 1 0 2 0 2 0]
[0 0 1 0 4 0 1 1 2 0 1 0 3 0 1 0]
[0 0 1 0 4 0 1 1 2 0 2 0 1 0 2 0]
[0 0 1 0 4 0 1 1 2 0 2 0 2 0 1 0]
[0 0 1 0 4 0 1

...

[4 0 2 0 3 0 3 0 4 0 4 0 1 2 1 0]
[4 0 2 0 3 0 4 0 1 1 1 2 4 0 4 0]
[4 0 2 0 3 0 4 0 1 1 4 0 4 0 1 2]
[4 0 2 0 3 0 4 0 1 2 1 2 4 0 2 1]
[4 0 2 0 3 0 4 0 1 2 4 0 4 0 1 1]
[4 0 2 0 3 0 4 0 2 1 4 0 1 2 1 2]
[4 0 2 0 3 0 4 0 4 0 4 0 1 2 1 1]
[4 0 2 0 4 0 0 0 1 1 1 1 3 0 3 0]
[4 0 2 0 4 0 0 0 1 1 3 0 3 0 1 1]
[4 0 2 0 4 0 0 0 3 0 3 0 1 1 1 1]
[4 0 2 0 4 0 1 0 1 1 1 1 3 0 4 0]
[4 0 2 0 4 0 1 0 1 1 1 1 4 0 3 0]
[4 0 2 0 4 0 1 0 1 1 1 2 3 0 3 0]
[4 0 2 0 4 0 1 0 1 1 3 0 3 0 1 2]
[4 0 2 0 4 0 1 0 1 1 3 0 4 0 1 1]
[4 0 2 0 4 0 1 0 1 1 4 0 3 0 1 1]
[4 0 2 0 4 0 1 0 1 2 1 1 3 0 3 0]
[4 0 2 0 4 0 1 0 1 2 3 0 3 0 1 1]
[4 0 2 0 4 0 1 0 3 0 3 0 1 1 1 2]
[4 0 2 0 4 0 1 0 3 0 3 0 1 2 1 1]
[4 0 2 0 4 0 1 0 3 0 4 0 1 1 1 1]
[4 0 2 0 4 0 1 0 4 0 3 0 1 1 1 1]
[4 0 2 0 4 0 1 1 1 1 1 2 3 0 4 0]
[4 0 2 0 4 0 1 1 1 1 4 0 3 0 1 2]
[4 0 2 0 4 0 1 1 1 2 1 1 3 0 4 0]
[4 0 2 0 4 0 1 1 1 2 1 1 4 0 3 0]
[4 0 2 0 4 0 1 1 1 2 3 0 3 0 1 2]
[4 0 2 0 4 0 1 1 1 2 3 0 4 0 1 1]
[4 0 2 0 4 0 1 1 3 0 4 0 1 1 1 2]
[4 0 2 0 4 0 1

[4 0 2 1 2 0 3 0 2 1 4 0 1 2 2 0]
[4 0 2 1 2 0 3 0 3 0 4 0 1 1 2 1]
[4 0 2 1 2 0 3 0 4 0 4 0 1 1 2 0]
[4 0 2 1 2 0 4 0 2 1 2 1 1 2 4 0]
[4 0 2 1 2 0 4 0 2 1 4 0 1 2 2 1]
[4 0 2 1 2 0 4 0 4 0 4 0 1 1 2 1]
[4 0 2 1 2 1 0 0 3 0 3 0 1 0 3 0]
[4 0 2 1 2 1 1 0 3 0 3 0 1 0 4 0]
[4 0 2 1 2 1 1 0 3 0 3 0 1 1 3 0]
[4 0 2 1 2 1 1 0 3 0 4 0 1 0 3 0]
[4 0 2 1 2 1 1 0 4 0 3 0 1 0 3 0]
[4 0 2 1 2 1 1 1 3 0 4 0 1 0 4 0]
[4 0 2 1 2 1 1 1 4 0 3 0 1 0 4 0]
[4 0 2 1 2 1 1 1 4 0 3 0 1 1 3 0]
[4 0 2 1 2 1 1 2 4 0 3 0 1 1 4 0]
[4 0 2 1 2 1 2 0 3 0 3 0 1 1 4 0]
[4 0 2 1 2 1 2 0 3 0 4 0 1 1 3 0]
[4 0 2 1 2 1 2 0 4 0 4 0 1 0 3 0]
[4 0 2 1 2 1 2 1 4 0 4 0 1 0 4 0]
[4 0 2 1 2 1 3 0 3 0 4 0 1 1 4 0]
[4 0 2 1 2 1 3 0 4 0 4 0 1 1 3 0]
[4 0 2 1 2 1 4 0 4 0 4 0 1 1 4 0]
[4 0 2 1 3 0 0 0 2 0 3 0 1 1 3 0]
[4 0 2 1 3 0 0 0 3 0 3 0 1 1 2 0]
[4 0 2 1 3 0 1 0 2 0 3 0 1 1 4 0]
[4 0 2 1 3 0 1 0 2 0 3 0 1 2 3 0]
[4 0 2 1 3 0 1 0 2 0 4 0 1 1 3 0]
[4 0 2 1 3 0 1 0 2 1 3 0 1 1 3 0]
[4 0 2 1 3 0 1 0 3 0 3 0 1 1 2 1]
[4 0 2 1 3 0 1

[4 0 3 0 1 1 1 0 1 1 2 0 3 0 2 1]
[4 0 3 0 1 1 1 0 1 1 2 0 4 0 2 0]
[4 0 3 0 1 1 1 0 1 1 2 1 2 0 3 0]
[4 0 3 0 1 1 1 0 1 1 2 1 3 0 2 0]
[4 0 3 0 1 1 1 0 1 1 3 0 2 0 3 0]
[4 0 3 0 1 1 1 0 1 2 2 0 2 0 3 0]
[4 0 3 0 1 1 1 0 1 2 2 0 3 0 2 0]
[4 0 3 0 1 1 1 0 2 0 3 0 2 0 1 2]
[4 0 3 0 1 1 1 0 2 0 3 0 2 1 1 1]
[4 0 3 0 1 1 1 0 2 0 4 0 2 0 1 1]
[4 0 3 0 1 1 1 0 2 1 3 0 2 0 1 1]
[4 0 3 0 1 1 1 0 3 0 2 0 2 0 1 2]
[4 0 3 0 1 1 1 0 3 0 2 0 2 1 1 1]
[4 0 3 0 1 1 1 0 3 0 2 0 3 0 1 1]
[4 0 3 0 1 1 1 0 3 0 2 0 4 0 1 0]
[4 0 3 0 1 1 1 0 3 0 2 1 2 0 1 1]
[4 0 3 0 1 1 1 0 3 0 2 1 3 0 1 0]
[4 0 3 0 1 1 1 0 4 0 2 0 2 0 1 1]
[4 0 3 0 1 1 1 0 4 0 2 0 3 0 1 0]
[4 0 3 0 1 1 1 1 1 0 4 0 2 0 4 0]
[4 0 3 0 1 1 1 1 1 1 2 1 2 0 4 0]
[4 0 3 0 1 1 1 1 1 1 2 1 3 0 2 1]
[4 0 3 0 1 1 1 1 1 1 3 0 2 0 4 0]
[4 0 3 0 1 1 1 1 1 1 3 0 2 1 3 0]
[4 0 3 0 1 1 1 1 1 2 2 0 2 0 4 0]
[4 0 3 0 1 1 1 1 1 2 2 0 2 1 3 0]
[4 0 3 0 1 1 1 1 1 2 2 0 3 0 2 1]
[4 0 3 0 1 1 1 1 1 2 2 0 4 0 2 0]
[4 0 3 0 1 1 1 1 2 0 4 0 2 0 1 2]
[4 0 3 0 1 1 1

[4 0 3 0 2 1 3 0 3 0 4 0 2 1 1 2]
[4 0 3 0 2 1 3 0 4 0 4 0 2 1 1 1]
[4 0 3 0 2 1 4 0 1 2 4 0 2 1 4 0]
[4 0 3 0 2 1 4 0 4 0 4 0 2 1 1 2]
[4 0 3 0 3 0 0 0 1 0 3 0 3 0 3 0]
[4 0 3 0 3 0 0 0 1 1 3 0 3 0 2 0]
[4 0 3 0 3 0 0 0 2 0 3 0 3 0 1 1]
[4 0 3 0 3 0 0 0 3 0 3 0 3 0 1 0]
[4 0 3 0 3 0 1 0 1 0 3 0 3 0 4 0]
[4 0 3 0 3 0 1 0 1 0 3 0 4 0 3 0]
[4 0 3 0 3 0 1 0 1 0 4 0 3 0 3 0]
[4 0 3 0 3 0 1 0 1 1 3 0 3 0 2 1]
[4 0 3 0 3 0 1 0 1 1 3 0 3 0 3 0]
[4 0 3 0 3 0 1 0 1 1 3 0 4 0 2 0]
[4 0 3 0 3 0 1 0 1 1 4 0 3 0 2 0]
[4 0 3 0 3 0 1 0 1 2 3 0 3 0 2 0]
[4 0 3 0 3 0 1 0 2 0 3 0 3 0 1 2]
[4 0 3 0 3 0 1 0 2 0 3 0 4 0 1 1]
[4 0 3 0 3 0 1 0 2 0 4 0 3 0 1 1]
[4 0 3 0 3 0 1 0 2 1 3 0 3 0 1 1]
[4 0 3 0 3 0 1 0 3 0 3 0 3 0 1 1]
[4 0 3 0 3 0 1 0 3 0 3 0 4 0 1 0]
[4 0 3 0 3 0 1 0 3 0 4 0 3 0 1 0]
[4 0 3 0 3 0 1 0 4 0 3 0 3 0 1 0]
[4 0 3 0 3 0 1 1 1 0 4 0 3 0 4 0]
[4 0 3 0 3 0 1 1 1 1 3 0 3 0 4 0]
[4 0 3 0 3 0 1 1 1 1 3 0 4 0 3 0]
[4 0 3 0 3 0 1 1 1 1 4 0 3 0 2 1]
[4 0 3 0 3 0 1 1 1 2 3 0 3 0 2 1]
[4 0 3 0 3 0 1

[4 0 4 0 1 2 3 0 3 0 2 1 4 0 4 0]
[4 0 4 0 1 2 3 0 4 0 2 1 4 0 3 0]
[4 0 4 0 1 2 4 0 4 0 2 1 4 0 4 0]
[4 0 4 0 2 0 0 0 2 0 2 0 3 0 3 0]
[4 0 4 0 2 0 0 0 2 0 3 0 3 0 2 0]
[4 0 4 0 2 0 0 0 3 0 3 0 2 0 2 0]
[4 0 4 0 2 0 1 0 2 0 2 0 3 0 4 0]
[4 0 4 0 2 0 1 0 2 0 2 0 4 0 3 0]
[4 0 4 0 2 0 1 0 2 0 2 1 3 0 3 0]
[4 0 4 0 2 0 1 0 2 0 3 0 3 0 2 1]
[4 0 4 0 2 0 1 0 2 0 3 0 4 0 2 0]
[4 0 4 0 2 0 1 0 2 0 4 0 3 0 2 0]
[4 0 4 0 2 0 1 0 2 1 2 0 3 0 3 0]
[4 0 4 0 2 0 1 0 2 1 3 0 3 0 2 0]
[4 0 4 0 2 0 1 0 3 0 3 0 2 0 2 1]
[4 0 4 0 2 0 1 0 3 0 3 0 2 1 2 0]
[4 0 4 0 2 0 1 0 3 0 4 0 2 0 2 0]
[4 0 4 0 2 0 1 0 4 0 3 0 2 0 2 0]
[4 0 4 0 2 0 1 1 2 0 2 1 3 0 4 0]
[4 0 4 0 2 0 1 1 2 0 4 0 3 0 2 1]
[4 0 4 0 2 0 1 1 2 1 2 0 3 0 4 0]
[4 0 4 0 2 0 1 1 2 1 2 0 4 0 3 0]
[4 0 4 0 2 0 1 1 2 1 3 0 3 0 2 1]
[4 0 4 0 2 0 1 1 2 1 3 0 4 0 2 0]
[4 0 4 0 2 0 1 1 3 0 4 0 2 0 2 1]
[4 0 4 0 2 0 1 1 4 0 3 0 2 0 2 1]
[4 0 4 0 2 0 1 1 4 0 3 0 2 1 2 0]
[4 0 4 0 2 0 1 2 2 1 2 0 4 0 4 0]
[4 0 4 0 2 0 1 2 2 1 3 0 4 0 2 1]
[4 0 4 0 2 0 1

In the first, we have the total of cases in data_x. The second line is the cases with tips that are truly unique with only one possible x. For example, $\left[ \begin{array}{cc}
1 & 1 \\
1 & 1 \\ \end{array} \right]$ have only one possible tip, which is \[22\] for the lines and \[22\] for the columns. Likewise,  $\left[ \begin{array}{cc} 
0 & 0 \\
0 & 0 \\ \end{array} \right]$ has the lines' tip \[00\] and for the columns \[00\].
The difference between these number is the number of cases we are expecting to fail. That is it 13174.

In [27]:
print(len(data_x))
print(len(unique))
print(len(data_x)-len(unique))

65536
52362
13174


This is an example of what is found in the dataset. The x is a concatenated array with the tips for the lines in the beginning and the tips for the columns in the half end. The board is printed afterward.

In [22]:
board = create_board(shape)
x = np.array(np.append(np.reshape(count_lines(board,shape), (-1)), np.reshape(count_rows(board,shape), (-1))))
x = x.reshape((1,-1))
print(x)
print(board)

[[1 0 2 0 1 1 1 1 1 0 1 0 1 0 4 0]]
[[0 0 0 1]
 [0 0 1 1]
 [0 1 0 1]
 [1 0 0 1]]


In [18]:
from keras.models import load_model

Using TensorFlow backend.


We test the trained model with the data above. We normalize the x array by dividing the max value possible which is to divide by the size of the line or column. In our case, we divide by 4.

With the predicted matrix we round it up. Notice that the model fails in the 4 number in the bottom left corner. That is because there is ambiguity in the tips for the first 2 column and the last 2 lines.

With the same tips or x, we could have guessed it to be $\left[ \begin{array}{cccc}
0 & 0 & 0 & 1\\
0 & 0 & 1 & 1\\
1 & 0 & 0 & 1\\
0 & 1 & 0 & 1\\ \end{array} \right]$. 

In [23]:
model = load_model('model_4x4.h5')

pred = model.predict(x/shape[0])
np.round((pred+1)/2)[0]

array([[0., 0., 0., 1.],
       [0., 0., 1., 1.],
       [1., 1., 0., 1.],
       [1., 1., 0., 1.]], dtype=float32)